# Connecting nodes using Monarch APIs
* https://api.monarchinitiative.org/api/#/
* https://scigraph-ontology.monarchinitiative.org/scigraph/docs/#/

There are different endpoints from which we can extract connections between entities:
- /association/find/[|/s_category/|/s_category/o_category/]. Get general associations. Inference (subclasses). Filters: s (id, taxa), o (id), with the last two api calls we can filter by categories.
- /association/from|to|between. Particular nodes required. Filters: categories and s (taxa), o (slim (superclasses))
- /bioentity/category/id:  jsonpath: \*_associations[\*].object.{id, label, ..}

In [1]:
import os, sys
import pandas as pd
import requests

In [2]:
# api addresses
biolink = 'https://api.monarchinitiative.org/api'
scigraph = 'https://scigraph-ontology.monarchinitiative.org/scigraph'

# path to data
path = os.getcwd() + '/data'
if not os.path.isdir(path): os.makedirs(path)

# read data
sys.path.insert(0, './data/')

## biolink::association 
* Examples from: https://github.com/biolink/biolink-api/blob/master/EXAMPLE-QUERIES.md

In [3]:
# endpoint
endpoint = '/association'

# get general associations: /find/
# generalized search over complete corpus of associations. Includes inferred by default (children associations). 
# It also takes into account alternatives IDs. 
# client query for all annotations in Monotremes (eg. Duck billed platypus). Excludes evidence
data = {'subject_taxon':'NCBITaxon:9255', 'fl_excludes_evidence':'true', 'rows':'10', 'page': '1'}
r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
r.headers

{'Access-Control-Allow-Origin': '*', 'Server': 'nginx/1.10.0 (Ubuntu)', 'Content-Type': 'application/json', 'Connection': 'keep-alive', 'Date': 'Thu, 15 Jun 2017 19:38:19 GMT', 'Content-Length': '15032'}

In [4]:
r.status_code

200

In [5]:
# read results 
r.json()

{'associations': [{'evidence_graph': {'edges': [{'obj': 'KEGG-path:map05150',
      'pred': 'RO:0002331',
      'sub': ':.well-known/genid/NCBIGene100079322product'},
     {'obj': ':.well-known/genid/NCBIGene100079322product',
      'pred': 'RO:0002205',
      'sub': 'NCBIGene:100079322'}],
    'nodes': [{'id': 'KEGG-path:map05150',
      'lbl': 'Staphylococcus aureus infection'},
     {'id': 'NCBIGene:100079322', 'lbl': 'ORAN-DRA'},
     {'id': ':.well-known/genid/NCBIGene100079322product', 'lbl': None}]},
   'evidence_types': None,
   'id': '6e44f56b-e7ac-426a-bd0f-7f0f9edde42d',
   'object': {'categories': None,
    'consider': None,
    'deprecated': None,
    'description': None,
    'id': 'KEGG-path:map05150',
    'label': 'Staphylococcus aureus infection',
    'replaced_by': None,
    'synonyms': None,
    'taxon': {'id': None, 'label': None},
    'types': None,
    'xrefs': None},
   'object_extension': None,
   'provided_by': ['https://data.monarchinitiative.org/ttl/ctd.ttl'],

In [6]:
# client query for disease-phenotype
data = {'subject':'OMIM:122440', 'object':'HP:0011927', 'fl_excludes_evidence':'true', 'rows':'10', 'page': '1'}
r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
r.json()

{'associations': [{'evidence_graph': {'edges': [{'obj': 'HP:0001156',
      'pred': 'RO:0002200',
      'sub': 'OMIM:122440'},
     {'obj': 'OMIM:122440',
      'pred': 'OBAN:association_has_subject',
      'sub': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8'},
     {'obj': 'HP:0001156',
      'pred': 'OBAN:association_has_object',
      'sub': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8'},
     {'obj': 'ECO:0000501',
      'pred': 'RO:0002558',
      'sub': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8'}],
    'nodes': [{'id': 'OMIM:122440', 'lbl': 'Stern-Lubinsky-Durrie syndrome'},
     {'id': 'ECO:0000501', 'lbl': 'evidence used in automatic assertion'},
     {'id': 'HP:0001156', 'lbl': 'Brachydactyly syndrome'},
     {'id': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8', 'lbl': None}]},
   'evidence_types': None,
   'id': 'e3f5b1bf-9197-408c-9ce3-1e30cb0658b8',
   'object': {'categories': None,
    'consider': None,
    'deprecated': None,
    'description': None

In [7]:
# get general associations between subject_category and object_category: /find/s_category/o_category/
# get gene-phenotype associations: /find/gene/phenotype/
# client query for mouse genes with abnormal Bowman membrane phenotype, i.e. cornea phenotypes
# (including subtypes in the ontology)
data = {'subject_taxon':'NCBITaxon:10090', 'object':'MP:0008521', 'rows':'10'}
r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
r.json()

{'associations': [{'evidence_graph': {'edges': [{'obj': 'MGI:2175208',
      'pred': 'OBAN:association_has_subject',
      'sub': 'MONARCH:3b7ff2e0515c2e2e1f40f78edb137bc0ba364b6a'},
     {'obj': 'ECO:0000006',
      'pred': 'RO:0002558',
      'sub': 'MONARCH:3b7ff2e0515c2e2e1f40f78edb137bc0ba364b6a'},
     {'obj': 'PMID:12714618',
      'pred': 'dc:source',
      'sub': 'MONARCH:3b7ff2e0515c2e2e1f40f78edb137bc0ba364b6a'},
     {'obj': 'MP:0008521', 'pred': 'RO:0002200', 'sub': 'MGI:2175208'},
     {'obj': 'MP:0008521',
      'pred': 'OBAN:association_has_object',
      'sub': 'MONARCH:3b7ff2e0515c2e2e1f40f78edb137bc0ba364b6a'}],
    'nodes': [{'id': 'MONARCH:3b7ff2e0515c2e2e1f40f78edb137bc0ba364b6a',
      'lbl': None},
     {'id': 'PMID:12714618', 'lbl': None},
     {'id': 'ECO:0000006', 'lbl': 'experimental evidence'},
     {'id': 'MGI:2175208',
      'lbl': 'Pax6<Sey-Neu>/Pax6<+> [involves: 102 * C3H]'},
     {'id': 'MP:0008521', 'lbl': 'abnormal Bowman membrane'}]},
   'evidence_

In [8]:
# client query for mouse genes with cornea phenotypes (including subtypes in the ontolgy), omitting evidence
data = {'subject_taxon':'NCBITaxon:10090', 'object':'MP:0008521', 'fl_excludes_evidence':'true', 'rows':'1000'}
r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
r.json()

{'associations': [{'evidence_graph': {'edges': [{'obj': 'MGI:2175208',
      'pred': 'OBAN:association_has_subject',
      'sub': 'MONARCH:3b7ff2e0515c2e2e1f40f78edb137bc0ba364b6a'},
     {'obj': 'ECO:0000006',
      'pred': 'RO:0002558',
      'sub': 'MONARCH:3b7ff2e0515c2e2e1f40f78edb137bc0ba364b6a'},
     {'obj': 'PMID:12714618',
      'pred': 'dc:source',
      'sub': 'MONARCH:3b7ff2e0515c2e2e1f40f78edb137bc0ba364b6a'},
     {'obj': 'MP:0008521', 'pred': 'RO:0002200', 'sub': 'MGI:2175208'},
     {'obj': 'MP:0008521',
      'pred': 'OBAN:association_has_object',
      'sub': 'MONARCH:3b7ff2e0515c2e2e1f40f78edb137bc0ba364b6a'}],
    'nodes': [{'id': 'MONARCH:3b7ff2e0515c2e2e1f40f78edb137bc0ba364b6a',
      'lbl': None},
     {'id': 'PMID:12714618', 'lbl': None},
     {'id': 'ECO:0000006', 'lbl': 'experimental evidence'},
     {'id': 'MGI:2175208',
      'lbl': 'Pax6<Sey-Neu>/Pax6<+> [involves: 102 * C3H]'},
     {'id': 'MP:0008521', 'lbl': 'abnormal Bowman membrane'}]},
   'evidence_

In [9]:
# client query for mouse genes with cornea phenotypes (using an HP ID), omitting evidence
data = {'subject_taxon':'NCBITaxon:10090', 'object':'HP:0000481', 'fl_excludes_evidence':'true', 'rows':'1000'}
r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
r.json()

{'associations': [{'evidence_graph': {'edges': [{'obj': 'HP:0011483',
      'pred': 'OBAN:association_has_object',
      'sub': 'MONARCH:699543a54807b872a1db881785bed63c40c3c1c3'},
     {'obj': 'HP:0011483', 'pred': 'RO:0002200', 'sub': 'MGI:3588509'},
     {'obj': 'PMID:10886015',
      'pred': 'dc:source',
      'sub': 'MONARCH:699543a54807b872a1db881785bed63c40c3c1c3'},
     {'obj': 'MGI:3588509',
      'pred': 'OBAN:association_has_subject',
      'sub': 'MONARCH:699543a54807b872a1db881785bed63c40c3c1c3'},
     {'obj': 'ECO:0000006',
      'pred': 'RO:0002558',
      'sub': 'MONARCH:699543a54807b872a1db881785bed63c40c3c1c3'}],
    'nodes': [{'id': 'PMID:10886015', 'lbl': None},
     {'id': 'ECO:0000006', 'lbl': 'experimental evidence'},
     {'id': 'MGI:3588509', 'lbl': 'Pax6<6Neu>/Pax6<+> [involves: 102 * C3H]'},
     {'id': 'MONARCH:699543a54807b872a1db881785bed63c40c3c1c3', 'lbl': None},
     {'id': 'HP:0011483',
      'lbl': 'Anterior synechiae of the anterior chamber'}]},
   '

In [10]:
# client query for human and mouse genes (mammalia taxon, ncbitaxon:40674) with eyelid abnormalities using HP, omitting evidence
data = {'subject_taxon':'NCBITaxon:40674', 'object':'HP:0000492', 'fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
r.json()

{'associations': [{'evidence_graph': {'edges': [{'obj': 'HP:0000508',
      'pred': 'RO:0002200',
      'sub': ':MONARCH:c000020'}],
    'nodes': [{'id': ':MONARCH:c000020', 'lbl': 'MONARCH:c000020'},
     {'id': 'HP:0000508', 'lbl': 'Ptosis'}]},
   'evidence_types': None,
   'id': '2c9bce48-b75c-48db-aaa4-0d3dc27cbd38',
   'object': {'categories': None,
    'consider': None,
    'deprecated': None,
    'description': None,
    'id': 'HP:0000508',
    'label': 'Ptosis',
    'replaced_by': None,
    'synonyms': None,
    'taxon': {'id': None, 'label': None},
    'types': None,
    'xrefs': None},
   'object_extension': None,
   'provided_by': ['http://data.monarchinitiative.org/ttl/udp.ttl'],
   'publications': None,
   'qualifiers': None,
   'relation': {'categories': None,
    'consider': None,
    'deprecated': None,
    'description': None,
    'id': 'RO:0002200',
    'label': 'has phenotype',
    'replaced_by': None,
    'synonyms': None,
    'types': None},
   'slim': None,
   'su

In [11]:
# client query for human and mouse genes with cardiovascular phenotypes using MP, omitting evidence
data = {'subject_taxon':'NCBITaxon:40674', 'object':'MP:0001340', 'fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
r.json()

{'associations': [{'evidence_graph': {'edges': [{'obj': 'HP:0000508',
      'pred': 'RO:0002200',
      'sub': ':MONARCH:c000020'}],
    'nodes': [{'id': ':MONARCH:c000020', 'lbl': 'MONARCH:c000020'},
     {'id': 'HP:0000508', 'lbl': 'Ptosis'}]},
   'evidence_types': None,
   'id': '2c9bce48-b75c-48db-aaa4-0d3dc27cbd38',
   'object': {'categories': None,
    'consider': None,
    'deprecated': None,
    'description': None,
    'id': 'HP:0000508',
    'label': 'Ptosis',
    'replaced_by': None,
    'synonyms': None,
    'taxon': {'id': None, 'label': None},
    'types': None,
    'xrefs': None},
   'object_extension': None,
   'provided_by': ['http://data.monarchinitiative.org/ttl/udp.ttl'],
   'publications': None,
   'qualifiers': None,
   'relation': {'categories': None,
    'consider': None,
    'deprecated': None,
    'description': None,
    'id': 'RO:0002200',
    'label': 'has phenotype',
    'replaced_by': None,
    'synonyms': None,
    'types': None},
   'slim': None,
   'su

In [12]:
sub = 'OMIM:122440'
obj = 'HP:0011927'

# get associations from a given particular source node (subject): /from/s_id
data = {'fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/from/{}'.format(biolink,endpoint,sub),data)
r.status_code, r.json()

(200,
 {'associations': [{'evidence_graph': {'edges': [{'obj': 'HP:0001156',
       'pred': 'RO:0002200',
       'sub': 'OMIM:122440'},
      {'obj': 'OMIM:122440',
       'pred': 'OBAN:association_has_subject',
       'sub': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8'},
      {'obj': 'HP:0001156',
       'pred': 'OBAN:association_has_object',
       'sub': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8'},
      {'obj': 'ECO:0000501',
       'pred': 'RO:0002558',
       'sub': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8'}],
     'nodes': [{'id': 'OMIM:122440', 'lbl': 'Stern-Lubinsky-Durrie syndrome'},
      {'id': 'ECO:0000501', 'lbl': 'evidence used in automatic assertion'},
      {'id': 'HP:0001156', 'lbl': 'Brachydactyly syndrome'},
      {'id': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8',
       'lbl': None}]},
    'evidence_types': None,
    'id': 'e3f5b1bf-9197-408c-9ce3-1e30cb0658b8',
    'object': {'categories': None,
     'consider': None,
     'deprecat

In [13]:
# get associations pointing to a given particular target node (object): /to/o_id
data = {'fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/to/{}'.format(biolink,endpoint,obj),data)
r.status_code, r.json()

(200,
 {'associations': [{'evidence_graph': {'edges': [{'obj': 'HP:0010034',
       'pred': 'RO:0002200',
       'sub': ':MONARCH:c000037'}],
     'nodes': [{'id': 'HP:0010034', 'lbl': 'Short 1st metacarpal'},
      {'id': ':MONARCH:c000037', 'lbl': 'MONARCH:c000037'}]},
    'evidence_types': None,
    'id': '668ad776-3e59-407b-af47-a0670790a1c9',
    'object': {'categories': None,
     'consider': None,
     'deprecated': None,
     'description': None,
     'id': 'HP:0010034',
     'label': 'Short 1st metacarpal',
     'replaced_by': None,
     'synonyms': None,
     'taxon': {'id': None, 'label': None},
     'types': None,
     'xrefs': None},
    'object_extension': None,
    'provided_by': ['http://data.monarchinitiative.org/ttl/udp.ttl'],
    'publications': None,
    'qualifiers': None,
    'relation': {'categories': None,
     'consider': None,
     'deprecated': None,
     'description': None,
     'id': 'RO:0002200',
     'label': 'has phenotype',
     'replaced_by': None,
  

In [14]:
# get (direct or indirect) connections between two given entities: /between/s_id/o_id
# it returns the association describing the connection
data = {'fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/between/{}/{}'.format(biolink,endpoint,sub,obj),data)
r.status_code, r.json()

(200,
 {'associations': [{'evidence_graph': {'edges': [{'obj': 'HP:0010034',
       'pred': 'RO:0002200',
       'sub': ':MONARCH:c000037'}],
     'nodes': [{'id': 'HP:0010034', 'lbl': 'Short 1st metacarpal'},
      {'id': ':MONARCH:c000037', 'lbl': 'MONARCH:c000037'}]},
    'evidence_types': None,
    'id': '668ad776-3e59-407b-af47-a0670790a1c9',
    'object': {'categories': None,
     'consider': None,
     'deprecated': None,
     'description': None,
     'id': 'HP:0010034',
     'label': 'Short 1st metacarpal',
     'replaced_by': None,
     'synonyms': None,
     'taxon': {'id': None, 'label': None},
     'types': None,
     'xrefs': None},
    'object_extension': None,
    'provided_by': ['http://data.monarchinitiative.org/ttl/udp.ttl'],
    'publications': None,
    'qualifiers': None,
    'relation': {'categories': None,
     'consider': None,
     'deprecated': None,
     'description': None,
     'id': 'RO:0002200',
     'label': 'has phenotype',
     'replaced_by': None,
  

In [15]:
# get (direct or indirect) connections between two given entities: /between/s_id/o_id
# it returns the association describing the connection
sub = 'NCBIGene:55768'
obj = 'OMIM:615273'
data = {'fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/between/{}/{}'.format(biolink,endpoint,sub,obj),data)
r.status_code, r.json()

(200,
 {'associations': [{'evidence_graph': {'edges': [{'obj': 'OMIM:615273',
       'pred': 'RO:0003301',
       'sub': 'Coriell:GM25331'}],
     'nodes': [{'id': 'OMIM:615273', 'lbl': 'NGLY1-deficiency'},
      {'id': 'Coriell:GM25331', 'lbl': 'NIGMS-GM25331'}]},
    'evidence_types': None,
    'id': '48fdd208-0180-49d8-8dbc-a3e2b6a9930e',
    'object': {'categories': None,
     'consider': None,
     'deprecated': None,
     'description': None,
     'id': 'OMIM:615273',
     'label': 'NGLY1-deficiency',
     'replaced_by': None,
     'synonyms': None,
     'taxon': {'id': None, 'label': None},
     'types': None,
     'xrefs': None},
    'object_extension': None,
    'provided_by': ['http://data.monarchinitiative.org/ttl/coriell.ttl'],
    'publications': None,
    'qualifiers': None,
    'relation': {'categories': None,
     'consider': None,
     'deprecated': None,
     'description': None,
     'id': 'RO:0003301',
     'label': 'is model of',
     'replaced_by': None,
     'syn

## biolink::bioentity

In [16]:
# endpoint
endpoint = '/bioentity'

data = {'use_compact_associations':'true', 'fl_excludes_evidence':'true'}
r = requests.get('{}{}/gene/NCBIGene:55768'.format(biolink,endpoint,sub),data)
r.status_code, r.json()
r.status_code, r.json()

(200,
 {'categories': ['gene', 'sequence feature'],
  'chromosome': {'categories': None,
   'consider': None,
   'deprecated': None,
   'description': None,
   'id': None,
   'label': None,
   'replaced_by': None,
   'synonyms': None,
   'taxon': {'id': None, 'label': None},
   'types': None,
   'xrefs': None},
  'consider': None,
  'deprecated': None,
  'description': None,
  'disease_associations': [{'evidence_graph': {'edges': [{'obj': ':.well-known/genid/genoGM25347',
       'pred': 'GENO:0000222',
       'sub': ':.well-known/genid/person-3200-1'},
      {'obj': 'NCBIGene:55768',
       'pred': 'GENO:0000418',
       'sub': 'ClinVarVariant:126423'},
      {'obj': ':.well-known/genid/610661.0004-610661.0005',
       'pred': 'GENO:0000382',
       'sub': ':.well-known/genid/genoGM25990'},
      {'obj': 'OMIM:615273',
       'pred': 'GENO:0000840',
       'sub': 'ClinVarVariant:50962'},
      {'obj': 'OMIM:615273',
       'pred': 'RO:0002200',
       'sub': ':.well-known/genid/person-

## Find connections between a matrix of entities

In [17]:
# endpoint
endpoint = '/association'

# get (direct or indirect) connections between two given entities: /between/s_id/o_id
# it returns the association describing the connection
sub = 'NCBIGene:55768'
obj = 'OMIM:615273'
data = {'fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/between/{}/{}'.format(biolink,endpoint,sub,obj),data)
r.status_code, r.json()

(200,
 {'associations': [{'evidence_graph': {'edges': [{'obj': 'OMIM:615273',
       'pred': 'RO:0003301',
       'sub': 'Coriell:GM25331'}],
     'nodes': [{'id': 'OMIM:615273', 'lbl': 'NGLY1-deficiency'},
      {'id': 'Coriell:GM25331', 'lbl': 'NIGMS-GM25331'}]},
    'evidence_types': None,
    'id': '48fdd208-0180-49d8-8dbc-a3e2b6a9930e',
    'object': {'categories': None,
     'consider': None,
     'deprecated': None,
     'description': None,
     'id': 'OMIM:615273',
     'label': 'NGLY1-deficiency',
     'replaced_by': None,
     'synonyms': None,
     'taxon': {'id': None, 'label': None},
     'types': None,
     'xrefs': None},
    'object_extension': None,
    'provided_by': ['http://data.monarchinitiative.org/ttl/coriell.ttl'],
    'publications': None,
    'qualifiers': None,
    'relation': {'categories': None,
     'consider': None,
     'deprecated': None,
     'description': None,
     'id': 'RO:0003301',
     'label': 'is model of',
     'replaced_by': None,
     'syn

In [18]:
# get (direct or indirect) connections between two given entities: /between/s_id/o_id
# it returns the association describing the connection
sub = 'NCBIGene:55768'
obj = 'OMIM:615273'
data = {'use_compact_associations':'true','fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/between/{}/{}'.format(biolink,endpoint,sub,obj),data)
r.status_code, r.json()

(200,
 {'associations': None,
  'compact_associations': [{'objects': ['OMIM:615273'],
    'relation': None,
    'subject': ':.well-known/genid/person-3259-1'},
   {'objects': ['OMIM:615273'],
    'relation': None,
    'subject': 'OMIM:610661.0002'},
   {'objects': ['OMIM:615273'],
    'relation': None,
    'subject': ':.well-known/genid/person-GM25990'},
   {'objects': ['OMIM:615273'], 'relation': None, 'subject': 'NCBIGene:55768'},
   {'objects': ['OMIM:615273'],
    'relation': 'RO:0003301',
    'subject': 'Coriell:GM25331'},
   {'objects': ['OMIM:615273'],
    'relation': None,
    'subject': 'OMIM:610661.0004'},
   {'objects': ['OMIM:615273'],
    'relation': 'RO:0003301',
    'subject': 'Coriell:GM25330'},
   {'objects': ['OMIM:615273'],
    'relation': None,
    'subject': 'OMIM:610661.0005'},
   {'objects': ['OMIM:615273'],
    'relation': 'RO:0002200',
    'subject': ':.well-known/genid/406885-404454VL'},
   {'objects': ['OMIM:615273'],
    'relation': None,
    'subject': 'OMI

In [19]:
sub = 'NCBIGene:55768'
obj = 'OMIM:615273'

In [20]:
# get associations from a given particular source node (subject): /from/s_id
data = {'fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/from/{}'.format(biolink,endpoint,sub),data)
r.status_code, r.json()

(200,
 {'associations': [{'evidence_graph': {'edges': [{'obj': 'ECO:0000304',
       'pred': 'RO:0002558',
       'sub': 'MONARCH:431a40f1d20afbb9e4c94aabb82bd8f2a7053342'},
      {'obj': 'NCBIGene:55768',
       'pred': 'OBAN:association_has_subject',
       'sub': 'MONARCH:431a40f1d20afbb9e4c94aabb82bd8f2a7053342'},
      {'obj': 'REACT:R-HSA-532668',
       'pred': 'RO:0002331',
       'sub': 'NCBIGene:55768'},
      {'obj': 'REACT:R-HSA-532668',
       'pred': 'OBAN:association_has_object',
       'sub': 'MONARCH:431a40f1d20afbb9e4c94aabb82bd8f2a7053342'}],
     'nodes': [{'id': 'ECO:0000304',
       'lbl': 'traceable author statement used in manual assertion'},
      {'id': 'NCBIGene:55768', 'lbl': 'NGLY1'},
      {'id': 'MONARCH:431a40f1d20afbb9e4c94aabb82bd8f2a7053342', 'lbl': None},
      {'id': 'REACT:R-HSA-532668',
       'lbl': 'N-glycan trimming in the ER and Calnexin/Calreticulin cycle'}]},
    'evidence_types': None,
    'id': '7b9b7ffd-9e85-494e-8f49-e5fbb7b7d508',
    '

In [21]:
# get associations from a given particular source node (subject): /from/s_id
data = {'use_compact_associations':'true','fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/from/{}'.format(biolink,endpoint,sub),data)
r.status_code, r.json()    

(200,
 {'associations': None,
  'compact_associations': [{'objects': ['GO:0046872', 'GO:0005515'],
    'relation': 'RO:0002327',
    'subject': 'NCBIGene:55768'},
   {'objects': ['GO:0006457',
     'KEGG-path:map04141',
     'GO:0006517',
     'REACT:R-HSA-532668'],
    'relation': 'RO:0002331',
    'subject': 'NCBIGene:55768'},
   {'objects': ['OMIM:615273'], 'relation': None, 'subject': 'NCBIGene:55768'},
   {'objects': ['GO:0005737', 'GO:0005634', 'GO:0005829'],
    'relation': 'BFO:0000050',
    'subject': 'NCBIGene:55768'}],
  'facet_counts': {},
  'facet_pivot': None,
  'numFound': None,
  'objects': None,
  'start': None})

In [22]:
# get associations pointing to a given particular target node (object): /to/o_id
data = {'fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/to/{}'.format(biolink,endpoint,obj),data)
r.status_code, r.json()

(200,
 {'associations': [{'evidence_graph': {'edges': [{'obj': 'OMIM:615273',
       'pred': 'RO:0003301',
       'sub': 'Coriell:GM25331'}],
     'nodes': [{'id': 'OMIM:615273', 'lbl': 'NGLY1-deficiency'},
      {'id': 'Coriell:GM25331', 'lbl': 'NIGMS-GM25331'}]},
    'evidence_types': None,
    'id': '48fdd208-0180-49d8-8dbc-a3e2b6a9930e',
    'object': {'categories': None,
     'consider': None,
     'deprecated': None,
     'description': None,
     'id': 'OMIM:615273',
     'label': 'NGLY1-deficiency',
     'replaced_by': None,
     'synonyms': None,
     'taxon': {'id': None, 'label': None},
     'types': None,
     'xrefs': None},
    'object_extension': None,
    'provided_by': ['http://data.monarchinitiative.org/ttl/coriell.ttl'],
    'publications': None,
    'qualifiers': None,
    'relation': {'categories': None,
     'consider': None,
     'deprecated': None,
     'description': None,
     'id': 'RO:0003301',
     'label': 'is model of',
     'replaced_by': None,
     'syn

In [23]:
# get associations pointing to a given particular target node (object): /to/o_id
data = {'use_compact_associations':'true','fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/to/{}'.format(biolink,endpoint,obj),data)
r.status_code, r.json()

(200,
 {'associations': None,
  'compact_associations': [{'objects': ['OMIM:615273'],
    'relation': None,
    'subject': ':.well-known/genid/person-3259-1'},
   {'objects': ['OMIM:615273'],
    'relation': None,
    'subject': 'OMIM:610661.0002'},
   {'objects': ['OMIM:615273'],
    'relation': None,
    'subject': ':.well-known/genid/person-GM25990'},
   {'objects': ['OMIM:615273'], 'relation': None, 'subject': 'NCBIGene:55768'},
   {'objects': ['OMIM:615273'],
    'relation': 'RO:0003301',
    'subject': 'Coriell:GM25331'},
   {'objects': ['OMIM:615273'],
    'relation': None,
    'subject': 'OMIM:610661.0004'},
   {'objects': ['OMIM:615273'],
    'relation': 'RO:0003301',
    'subject': 'Coriell:GM25330'},
   {'objects': ['OMIM:615273'],
    'relation': None,
    'subject': 'OMIM:610661.0005'},
   {'objects': ['OMIM:615273'],
    'relation': 'RO:0002200',
    'subject': ':.well-known/genid/406885-404454VL'},
   {'objects': ['OMIM:615273'],
    'relation': None,
    'subject': 'OMI

In [24]:
# get associations using find/. test the use_compact parameter. test how the inference changes results
data = {'subject':'NCBIGene:55768','object':'OMIM:615273','use_compact_associations':'true','fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
r.json()

{'associations': [{'evidence_graph': {'edges': [{'obj': ':.well-known/genid/genoGM25347',
      'pred': 'GENO:0000222',
      'sub': ':.well-known/genid/person-3200-1'},
     {'obj': 'NCBIGene:55768',
      'pred': 'GENO:0000418',
      'sub': 'ClinVarVariant:126423'},
     {'obj': ':.well-known/genid/610661.0004-610661.0005',
      'pred': 'GENO:0000382',
      'sub': ':.well-known/genid/genoGM25990'},
     {'obj': 'OMIM:615273',
      'pred': 'GENO:0000840',
      'sub': 'ClinVarVariant:50962'},
     {'obj': 'OMIM:615273',
      'pred': 'RO:0002200',
      'sub': ':.well-known/genid/person-3200-1'},
     {'obj': 'OMIM:615273',
      'pred': 'RO:0002200',
      'sub': ':.well-known/genid/OMIM610661-615273VL'},
     {'obj': ':.well-known/genid/person-3200-1',
      'pred': 'OBAN:association_has_subject',
      'sub': 'MONARCH:42d05e731935a651eaf999c2aeb046987f01cca7'},
     {'obj': 'OMIM:615273',
      'pred': 'OBAN:association_has_object',
      'sub': 'MONARCH:a78544aa0feaec55807c289

In [25]:
# get associations using find/. test the use_compact parameter. test how the inference changes results
data = {'subject':'NCBIGene:55768','use_compact_associations':'true','fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
r.json()

{'associations': [{'evidence_graph': {'edges': [{'obj': 'ECO:0000304',
      'pred': 'RO:0002558',
      'sub': 'MONARCH:431a40f1d20afbb9e4c94aabb82bd8f2a7053342'},
     {'obj': 'NCBIGene:55768',
      'pred': 'OBAN:association_has_subject',
      'sub': 'MONARCH:431a40f1d20afbb9e4c94aabb82bd8f2a7053342'},
     {'obj': 'REACT:R-HSA-532668',
      'pred': 'RO:0002331',
      'sub': 'NCBIGene:55768'},
     {'obj': 'REACT:R-HSA-532668',
      'pred': 'OBAN:association_has_object',
      'sub': 'MONARCH:431a40f1d20afbb9e4c94aabb82bd8f2a7053342'}],
    'nodes': [{'id': 'ECO:0000304',
      'lbl': 'traceable author statement used in manual assertion'},
     {'id': 'NCBIGene:55768', 'lbl': 'NGLY1'},
     {'id': 'MONARCH:431a40f1d20afbb9e4c94aabb82bd8f2a7053342', 'lbl': None},
     {'id': 'REACT:R-HSA-532668',
      'lbl': 'N-glycan trimming in the ER and Calnexin/Calreticulin cycle'}]},
   'evidence_types': None,
   'id': '7b9b7ffd-9e85-494e-8f49-e5fbb7b7d508',
   'object': {'categories': Non

In [26]:
# get associations using find/. test the use_compact parameter. test how the inference changes results
data = {'object':'OMIM:615273','use_compact_associations':'true','fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
r.json()

{'associations': [{'evidence_graph': {'edges': [{'obj': 'OMIM:615273',
      'pred': 'RO:0003301',
      'sub': 'Coriell:GM25331'}],
    'nodes': [{'id': 'OMIM:615273', 'lbl': 'NGLY1-deficiency'},
     {'id': 'Coriell:GM25331', 'lbl': 'NIGMS-GM25331'}]},
   'evidence_types': None,
   'id': '48fdd208-0180-49d8-8dbc-a3e2b6a9930e',
   'object': {'categories': None,
    'consider': None,
    'deprecated': None,
    'description': None,
    'id': 'OMIM:615273',
    'label': 'NGLY1-deficiency',
    'replaced_by': None,
    'synonyms': None,
    'taxon': {'id': None, 'label': None},
    'types': None,
    'xrefs': None},
   'object_extension': None,
   'provided_by': ['http://data.monarchinitiative.org/ttl/coriell.ttl'],
   'publications': None,
   'qualifiers': None,
   'relation': {'categories': None,
    'consider': None,
    'deprecated': None,
    'description': None,
    'id': 'RO:0003301',
    'label': 'is model of',
    'replaced_by': None,
    'synonyms': None,
    'types': None},
  

In [27]:
# get associations using find/. test the use_compact parameter. test how the inference changes results
data = {'subject':'OMIM:122440'}
r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
r.json()

{'associations': [{'evidence_graph': {'edges': [{'obj': 'HP:0001156',
      'pred': 'RO:0002200',
      'sub': 'OMIM:122440'},
     {'obj': 'OMIM:122440',
      'pred': 'OBAN:association_has_subject',
      'sub': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8'},
     {'obj': 'HP:0001156',
      'pred': 'OBAN:association_has_object',
      'sub': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8'},
     {'obj': 'ECO:0000501',
      'pred': 'RO:0002558',
      'sub': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8'}],
    'nodes': [{'id': 'OMIM:122440', 'lbl': 'Stern-Lubinsky-Durrie syndrome'},
     {'id': 'ECO:0000501', 'lbl': 'evidence used in automatic assertion'},
     {'id': 'HP:0001156', 'lbl': 'Brachydactyly syndrome'},
     {'id': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8', 'lbl': None}]},
   'evidence_types': None,
   'id': 'e3f5b1bf-9197-408c-9ce3-1e30cb0658b8',
   'object': {'categories': None,
    'consider': None,
    'deprecated': None,
    'description': None

In [28]:
# get associations from a given particular source node (subject): /from/s_id
sub = 'OMIM:122440'
data = {'use_compact_associations':'true','fl_excludes_evidence':'true'}
r = requests.get('{}{}/from/{}'.format(biolink,endpoint,sub),data)
r.status_code, r.json()    

(200,
 {'associations': None,
  'compact_associations': [{'objects': ['HP:0001019',
     'HP:0000613',
     'HP:0001131',
     'HP:0000972',
     'HP:0004322',
     'HP:0000164',
     'HP:0009882',
     'HP:0001622',
     'HP:0001156',
     'HP:0001806'],
    'relation': 'RO:0002200',
    'subject': 'OMIM:122440'}],
  'facet_counts': {},
  'facet_pivot': None,
  'numFound': None,
  'objects': None,
  'start': None})

In [29]:
# get associations using find/. test the use_compact parameter. test how the inference changes results
data = {'object':'HP:0011927'}
r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
r.json()

{'associations': [{'evidence_graph': {'edges': [{'obj': 'HP:0010034',
      'pred': 'RO:0002200',
      'sub': ':MONARCH:c000037'}],
    'nodes': [{'id': 'HP:0010034', 'lbl': 'Short 1st metacarpal'},
     {'id': ':MONARCH:c000037', 'lbl': 'MONARCH:c000037'}]},
   'evidence_types': None,
   'id': '668ad776-3e59-407b-af47-a0670790a1c9',
   'object': {'categories': None,
    'consider': None,
    'deprecated': None,
    'description': None,
    'id': 'HP:0010034',
    'label': 'Short 1st metacarpal',
    'replaced_by': None,
    'synonyms': None,
    'taxon': {'id': None, 'label': None},
    'types': None,
    'xrefs': None},
   'object_extension': None,
   'provided_by': ['http://data.monarchinitiative.org/ttl/udp.ttl'],
   'publications': None,
   'qualifiers': None,
   'relation': {'categories': None,
    'consider': None,
    'deprecated': None,
    'description': None,
    'id': 'RO:0002200',
    'label': 'has phenotype',
    'replaced_by': None,
    'synonyms': None,
    'types': No

In [30]:
# get associations pointing to a given particular target node (object): /to/o_id
obj = 'HP:0011927'
data = {'use_compact_associations':'true','fl_excludes_evidence':'true'}
r = requests.get('{}{}/to/{}'.format(biolink,endpoint,obj),data)
r.status_code, r.json()

(200,
 {'associations': None,
  'compact_associations': [{'objects': ['HP:0001156'],
    'relation': 'RO:0002200',
    'subject': 'OMIM:187600'},
   {'objects': ['HP:0005819'],
    'relation': 'RO:0002200',
    'subject': 'OMIM:210720'},
   {'objects': ['HP:0001156'],
    'relation': 'RO:0002200',
    'subject': 'OMIM:251450'},
   {'objects': ['HP:0005819'],
    'relation': 'RO:0002200',
    'subject': 'OMIM:182255'},
   {'objects': ['HP:0001156'],
    'relation': 'RO:0002200',
    'subject': 'OMIM:122440'},
   {'objects': ['HP:0010034'],
    'relation': 'RO:0002200',
    'subject': ':MONARCH:c000037'},
   {'objects': ['HP:0001156'],
    'relation': 'RO:0002200',
    'subject': 'OMIM:258480'},
   {'objects': ['HP:0001156'],
    'relation': 'RO:0002200',
    'subject': 'OMIM:102370'},
   {'objects': ['HP:0001156'],
    'relation': 'RO:0002200',
    'subject': 'Orphanet:2145'},
   {'objects': ['HP:0001831'],
    'relation': 'RO:0002200',
    'subject': ':MONARCH:c000019'}],
  'facet_coun

In [31]:
# get s->o
# get (direct or indirect) connections between two given entities: /between/s_id/o_id
# it returns the association describing the connection
sub_l = ['NCBIGene:55768','UBERON:0000007']
obj_l = ['OMIM:615273','HP:0001252','HP:0001263']
data = {'use_compact_associations':'true','fl_excludes_evidence':'true', 'page':'1'}
for sub in sub_l:
    for obj in obj_l:
        r = requests.get('{}{}/between/{}/{}'.format(biolink,endpoint,sub,obj),data)
        print(r.status_code, r.json()['compact_associations'])

200 [{'objects': ['OMIM:615273'], 'relation': None, 'subject': ':.well-known/genid/person-3259-1'}, {'objects': ['OMIM:615273'], 'relation': None, 'subject': 'OMIM:610661.0002'}, {'objects': ['OMIM:615273'], 'relation': None, 'subject': ':.well-known/genid/person-GM25990'}, {'objects': ['OMIM:615273'], 'relation': None, 'subject': 'NCBIGene:55768'}, {'objects': ['OMIM:615273'], 'relation': 'RO:0003301', 'subject': 'Coriell:GM25331'}, {'objects': ['OMIM:615273'], 'relation': None, 'subject': 'OMIM:610661.0004'}, {'objects': ['OMIM:615273'], 'relation': 'RO:0003301', 'subject': 'Coriell:GM25330'}, {'objects': ['OMIM:615273'], 'relation': None, 'subject': 'OMIM:610661.0005'}, {'objects': ['OMIM:615273'], 'relation': 'RO:0002200', 'subject': ':.well-known/genid/406885-404454VL'}, {'objects': ['OMIM:615273'], 'relation': None, 'subject': 'OMIM:610661.0003'}]
200 [{'objects': ['HP:0008936'], 'relation': 'RO:0002200', 'subject': ':MONARCH:c000011'}, {'objects': ['HP:0001290'], 'relation': 'RO

In [32]:
sub_l = ['UBERON:0000007']
obj_l = ['HP:0001252']
data = {'use_compact_associations':'true','fl_excludes_evidence':'true', 'page':'1'}
for sub in sub_l:
    for obj in obj_l:
        r = requests.get('{}{}/between/{}/{}'.format(biolink,endpoint,sub,obj),data)
        print(r.status_code, r.json()['compact_associations'])

200 [{'objects': ['HP:0008936'], 'relation': 'RO:0002200', 'subject': ':MONARCH:c000011'}, {'objects': ['HP:0001290'], 'relation': 'RO:0002200', 'subject': ':MONARCH:c000025'}, {'objects': ['HP:0001290'], 'relation': 'RO:0002200', 'subject': ':MONARCH:c000006'}, {'objects': ['HP:0001290'], 'relation': 'RO:0002200', 'subject': ':MONARCH:c000005'}, {'objects': ['HP:0006829'], 'relation': 'RO:0002200', 'subject': ':MONARCH:c000013'}, {'objects': ['HP:0008936'], 'relation': 'RO:0002200', 'subject': ':MONARCH:c000037'}, {'objects': ['HP:0030190', 'HP:0001290'], 'relation': 'RO:0002200', 'subject': ':MONARCH:c000026'}, {'objects': ['HP:0001290'], 'relation': 'RO:0002200', 'subject': ':MONARCH:c000020'}, {'objects': ['HP:0006829'], 'relation': 'RO:0002200', 'subject': ':MONARCH:c000021'}]


In [33]:
sub_l = ['UBERON:0000007']
obj_l = ['HP:0001252']
for sub in sub_l:
    for obj in obj_l:
        data = {'object':obj, 'subject':sub, 'page':'1'}
        r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
        print(r.json())

{'objects': None, 'start': None, 'compact_associations': None, 'facet_counts': {'object_closure': {}, 'subject_taxon_label': {}}, 'facet_pivot': None, 'numFound': None, 'associations': []}


In [34]:
sub_l = ['OMIM:122440']
obj_l = ['HP:0011927']
data = {'use_compact_associations':'true','fl_excludes_evidence':'true', 'page':'1'}
for sub in sub_l:
    for obj in obj_l:
        r = requests.get('{}{}/between/{}/{}'.format(biolink,endpoint,sub,obj),data)
        print(r.status_code, r.json()['compact_associations'])

200 [{'objects': ['HP:0001156'], 'relation': 'RO:0002200', 'subject': 'OMIM:187600'}, {'objects': ['HP:0005819'], 'relation': 'RO:0002200', 'subject': 'OMIM:210720'}, {'objects': ['HP:0001156'], 'relation': 'RO:0002200', 'subject': 'OMIM:251450'}, {'objects': ['HP:0005819'], 'relation': 'RO:0002200', 'subject': 'OMIM:182255'}, {'objects': ['HP:0001156'], 'relation': 'RO:0002200', 'subject': 'OMIM:122440'}, {'objects': ['HP:0010034'], 'relation': 'RO:0002200', 'subject': ':MONARCH:c000037'}, {'objects': ['HP:0001156'], 'relation': 'RO:0002200', 'subject': 'OMIM:258480'}, {'objects': ['HP:0001156'], 'relation': 'RO:0002200', 'subject': 'OMIM:102370'}, {'objects': ['HP:0001156'], 'relation': 'RO:0002200', 'subject': 'Orphanet:2145'}, {'objects': ['HP:0001831'], 'relation': 'RO:0002200', 'subject': ':MONARCH:c000019'}]


In [35]:
sub_l = ['OMIM:122440']
obj_l = ['HP:0011927']
for sub in sub_l:
    for obj in obj_l:
        data = {'object':obj, 'subject':sub, 'page':'1'}
        r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
        print(r.json()['associations'])

[{'object': {'xrefs': None, 'consider': None, 'description': None, 'types': None, 'taxon': {'id': None, 'label': None}, 'synonyms': None, 'label': 'Brachydactyly syndrome', 'categories': None, 'id': 'HP:0001156', 'deprecated': None, 'replaced_by': None}, 'type': None, 'evidence_graph': {'nodes': [{'lbl': 'Stern-Lubinsky-Durrie syndrome', 'id': 'OMIM:122440'}, {'lbl': 'evidence used in automatic assertion', 'id': 'ECO:0000501'}, {'lbl': 'Brachydactyly syndrome', 'id': 'HP:0001156'}, {'lbl': None, 'id': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8'}], 'edges': [{'pred': 'RO:0002200', 'obj': 'HP:0001156', 'sub': 'OMIM:122440'}, {'pred': 'OBAN:association_has_subject', 'obj': 'OMIM:122440', 'sub': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8'}, {'pred': 'OBAN:association_has_object', 'obj': 'HP:0001156', 'sub': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8'}, {'pred': 'RO:0002558', 'obj': 'ECO:0000501', 'sub': 'MONARCH:80ff45a88f23791464bc2b6b5e760a0c987c9de8'}]}, 'qualifiers

In [36]:
# do not use between/ call

In [ ]:
# benchmarking both algorithms

In [41]:
from tqdm import tqdm
from itertools import product

In [50]:
# 1st algorithm
# s -> o
sub_l = ['NCBIGene:55768'] * 10
obj_l = ['OMIM:615273'] * 10

stuff = product(sub_l, obj_l)
for sub, obj in tqdm(stuff, total=len(sub_l) * len(obj_l)):
        data = {'object':obj, 'subject':sub, 'page':'1'}
        r = requests.get('{}{}/find/'.format(biolink,endpoint),data)

# o -> s
sub_l = ['NCBIGene:55768'] * 10
obj_l = ['OMIM:615273'] * 10

stuff = product(obj_l, sub_l)
for sub, obj in tqdm(stuff, total=len(sub_l) * len(obj_l)):
        data = {'object':sub, 'subject':obj, 'page':'1'}
        r = requests.get('{}{}/find/'.format(biolink,endpoint),data)

100%|██████████| 100/100 [00:26<00:00,  4.17it/s]


In [ ]:
# 2nd algorithm
sub_l = ['NCBIGene:55768'] * 10
obj_l = ['OMIM:615273'] * 10

# out edges: from/
data = {'use_compact_associations':'true','fl_excludes_evidence':'true', 'page':'1'}
r = requests.get('{}{}/from/{}'.format(biolink,endpoint,sub),data)

# in edges: to/
data = {'use_compact_associations':'true','fl_excludes_evidence':'true'}
r = requests.get('{}{}/to/{}'.format(biolink,endpoint,obj),data)

# overlap with network

In [37]:
# 1st ALGORITHM
## Search for links between 1300x1300: find/{subject}/{object}/

In [38]:
# get s->o

In [49]:
sub_l = ['NCBIGene:55768']
obj_l = ['OMIM:615273'] 

for sub in sub_l:
    for obj in obj_l:
            data = {'object':obj, 'subject':sub, 'page':'1'}
            r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
            print(r.json()['associations'])

[{'object': {'xrefs': None, 'consider': None, 'description': None, 'types': None, 'taxon': {'id': None, 'label': None}, 'synonyms': None, 'label': 'NGLY1-deficiency', 'categories': None, 'id': 'OMIM:615273', 'deprecated': None, 'replaced_by': None}, 'type': None, 'evidence_graph': {'nodes': [{'lbl': 'affected male proband with Congenital disorder of deglycosylation', 'id': ':.well-known/genid/person-3199-1'}, {'lbl': 'NM_001145294.1(NGLY1):c.1079_1081delGAA (p.Arg360del)', 'id': 'ClinVarVariant:126423'}, {'lbl': 'affected female proband with Congenital disorder of deglycosylation', 'id': ':.well-known/genid/person-3213-1'}, {'lbl': 'NGLY1;NGLY1(3-BP DEL  1205 TTC;ARG542TER  c.1570C>T)', 'id': ':.well-known/genid/610661.0004-610661.0005'}, {'lbl': None, 'id': 'MONARCH:a78544aa0feaec55807c289ba3d6aedadb69dbd8'}, {'lbl': 'NM_018297.3(NGLY1):c.1891delC (p.Gln631Serfs)', 'id': 'ClinVarVariant:50961'}, {'lbl': 'NGLY1;NGLY1(ARG401TER;c.1891delC)', 'id': ':.well-known/genid/610661.0001-610661.

In [43]:
# get o->s

In [44]:
sub_l = ['OMIM:615273']
obj_l = ['NCBIGene:55768']
for sub in sub_l:
    for obj in obj_l:
        data = {'object':obj, 'subject':sub, 'page':'1'}
        r = requests.get('{}{}/find/'.format(biolink,endpoint),data)
        print(r.json()['associations'])

[]


In [45]:
# 2nd ALGORITHM
## Search for links between 1300x1300: 1) to/from  2) match network